In [1]:
import panel as pn
import geopandas as gpd
import pandas as pd
import folium
import param
from shapely.geometry import Point, Polygon
pn.extension()

In [2]:
acs = gpd.read_parquet('../data/acs.parquet')

In [3]:
food = pd.read_csv('../data/food_source_data_set.csv')

In [4]:
see = food.head(100)

In [5]:
see_geo = gpd.GeoDataFrame(
    see, geometry=gpd.points_from_xy(see.longitude, see.latitude))
see_geo.dropna(inplace=True)

In [6]:
acs[acs.year == 2019].explore('median_home_value', 
                              scheme="quantiles",  # use mapclassify's natural breaks scheme
                              #cmap='Greens',
                              legend=True, # show legend
                              k=5, # use 5 bins
                              legend_kwds=dict(colorbar=False),
                              tooltip='median_household_income')

In [7]:
acs = acs[['GEOID', 'geometry', 'year', 'tract', 'total_pop', 'n_white', 'n_black', 'n_asian', 'n_hispanic', 'n_poverty',
           'median_household_income', 'median_home_value', 'p_poverty', 'p_black','p_white', 'p_hispanic', 'p_asian' ]]

In [8]:
columns = list(acs.columns[-7:])

In [9]:
def base_map():
    return folium.Map(location=[41.87494504366721, -87.62871556344562], zoom_level=5)
def attr_map(m_obj, attr, year):
    return acs[acs.year == year].explore(m = m_obj, column= attr, scheme="quantiles", 
                                         legend=True, k=5, legend_kwds=dict(colorbar=False), tooltip=attr)
def food_map(m_obj):
    return see_geo.explore(m=m_obj, tooltip=['dba_name', 'facility_type'])
def build_map(attr, year):
    chi = food_map(attr_map(base_map(), attr, year))
    folium.LayerControl().add_to(chi)
    return chi

In [10]:
chi = build_map('p_white',2019)

In [11]:
chi

In [20]:
class FoliumPanel(param.Parameterized):
    attribute = param.Selector(default ='median_household_income', objects=columns)
    year = param.Selector(default=2019, objects=list(acs.year.unique()))

    def __init__(self, **params):
        super().__init__(**params)
        self.folium_pane = pn.pane.plot.Folium(sizing_mode="stretch_both", min_height=800, margin=0)    
        self.view = pn.Row(
            pn.Column('# Chicago Eats', self.folium_pane, sizing_mode='stretch_both'),
            pn.Column(self.param.attribute, self.param.year, height=300, width=400)
            ).servable()
        self.map = build_map(self.attribute, self.year)
        self._update_map()

    @param.depends('attribute', 'year', watch=True)
    def _update_map(self):
        self.map = build_map(self.attribute, self.year)
        self.folium_pane.object = self.map

app = FoliumPanel()
app.view

BokehModel(combine_events=True, render_bundle={'docs_json': {'1bf5f295-3198-4f3b-92ef-4a749721a434': {'defs': …

Row(sizing_mode='stretch_width')
    [0] Column(sizing_mode='stretch_both')
        [0] Markdown(str, sizing_mode='stretch_width')
        [1] Folium(Map, margin=0, min_height=800, sizing_mode='stretch_both')
    [1] Column(height=300, sizing_mode='fixed', width=400)
        [0] Select(name='Attribute', options=OrderedDict([('median_hous...]), sizing_mode='stretch_width', value='median_household_income')
        [1] Select(name='Year', options=OrderedDict([('2013', ...]), sizing_mode='stretch_width', value=2019)